In [5]:
import torch
import yaml
import os

# Humandoid MARL
from Humanoid_MARL.envs.base_env import GymWrapper, VectorGymWrapper
from Humanoid_MARL.utils.torch_utils import save_models, load_models
from Humanoid_MARL.agent.ppo.train_torch import Agent, eval_unroll, get_agent_actions
from Humanoid_MARL.envs.torch_wrapper import TorchWrapper
from IPython.display import HTML, clear_output
from brax.io import html
import jax
from Humanoid_MARL import envs
from Humanoid_MARL.utils.utils import load_reward_config, load_config

In [6]:
env_name = "ants"
config = load_config(env_name)
env = envs.create(config['env_name'], auto_reset=True, **config['env_config'])
env = GymWrapper(env, get_jax_state=True)
env = TorchWrapper(env, device=config['train_config']['device'], get_jax_state=True)

model = "models/20240331_120100_ppo_ants.pt"
model_path = os.path.join("../", model)
# env warmup
observation = env.reset()
action = torch.zeros(env.action_space.shape[0] * env.num_agents).to(config['train_config']['device'])
env.step(action)
agents = load_models(model_path, Agent, device=config['train_config']['device'])
jax_states = []
num_steps = 1000

eval_reward = 0.0
episodes = torch.zeros((), device = config['train_config']['device'])
for i in range(num_steps):
    print(f"{i} / {num_steps}")
    logits, action = get_agent_actions(agents, observation, env.obs_dims)
    if config['agent_config'].get("freeze_idx"):
        action[:,config['agent_config'].get("freeze_idx") * 8:(config['agent_config'].get("freeze_idx") * 8) + 8] =  torch.ones_like(action[:,config['agent_config'].get("freeze_idx") * 8:(config['agent_config'].get("freeze_idx") * 8) + 8]) * 0
    jax_state, observation, reward, done, info = env.step(Agent.dist_postprocess(action[0]))
    episodes += torch.sum(done)
    jax_states.append(jax_state)
    print(f"{i} | {info} | DONE [{done}] | Reward [{reward}]")
    eval_reward += reward
    if done:
        observation = env.reset()
        print(f"Episode Done")
        print(f"Total Reward | {eval_reward / episodes}")
print(f"Total Reward | {eval_reward / episodes}")

Models loaded from ../models/20240331_120100_ppo_ants.pt
0 / 1000
0 | {'distance_from_origin': tensor([0.0804, 2.9239], device='cuda:0'), 'first_obs': tensor([-4.6000e-03,  8.6061e-02,  4.8164e-01,  1.9255e-01,  3.6793e-01,
         4.5683e-01,  3.8132e-01,  6.5545e-01,  4.3182e-01, -2.8743e-01,
         2.8326e-01,  4.7448e-01, -5.6083e-01,  4.9329e-01,  4.6618e-01,
        -2.0175e-01, -1.9580e-01,  5.0645e-01, -3.7164e-01, -4.9484e-01,
         5.3182e-01,  2.7823e-01, -1.1113e-01,  4.8880e-01,  5.7399e-01,
        -2.8842e-01,  4.9423e-01,  2.9516e+00, -1.3025e-02,  4.5651e-01,
         3.1645e+00,  1.7869e-01,  4.3440e-01,  3.3743e+00,  3.7391e-01,
         4.1224e-01,  2.7591e+00,  2.0036e-01,  4.5311e-01,  2.5667e+00,
         4.1374e-01,  4.4971e-01,  2.7387e+00, -2.0474e-01,  4.7862e-01,
         2.5270e+00, -3.9784e-01,  5.0075e-01,  3.1441e+00, -2.2641e-01,
         4.5991e-01,  3.3291e+00, -4.4624e-01,  4.6407e-01, -6.4604e-02,
         2.6472e-02, -5.1049e-02, -1.1553e-01,

In [7]:
HTML(html.render(env.sys, [jax_state.pipeline_state for jax_state in jax_states])) 

In [8]:
HTML(html.render(env.sys, [jax_state.pipeline_state for jax_state in jax_states])) 